<a href="https://colab.research.google.com/github/Lorenzo-Gandini/culture-classifier/blob/main/HW1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Import of all the libraries
!pip install wget wikidata # to download data

from sklearn.decomposition import PCA
from torch import FloatTensor as FT
from torch import LongTensor as LT
from tqdm.auto import tqdm
from wikidata.client import Client

import matplotlib.pyplot as plt
import torch.nn as nn
import collections
import numpy as np
import pandas as pd
import torch
import json
import os
import re
import wget


In [ ]:
from google.colab import drive
drive.mount('/content/drive/')
root_folder = '/content/drive/My Drive/nlp_data/' # to save checkpoints
data_path = '/content/drive/MyDrive/HOMEWORK_1/[MNLP 2025 HW1] train set [PUBLIC] - train_cleaned.tsv'
gold_dataset = pd.read_csv(data_path, sep='\t')

Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [ ]:
client = Client()

all_properties = set()
items_map = {}

for idx, row in gold_dataset.iterrows():
  item_url = row['item']
  qid = item_url.split('/')[-1]

  entity = client.get(qid, load=True)
  data = entity.attributes

  print(data)

  #item_properties = set(data.keys())


{'pageid': 493, 'ns': 0, 'title': 'Q306', 'lastrevid': 2327133464, 'modified': '2025-03-19T12:40:37Z', 'type': 'item', 'id': 'Q306', 'labels': {'es': {'language': 'es', 'value': 'Sebastián Piñera'}, 'en': {'language': 'en', 'value': 'Sebastián Piñera'}, 'fr': {'language': 'fr', 'value': 'Sebastián Piñera'}, 'ru': {'language': 'ru', 'value': 'Себастьян Пиньера'}, 'de': {'language': 'de', 'value': 'Sebastián Piñera'}, 'it': {'language': 'it', 'value': 'Sebastián Piñera'}, 'ar': {'language': 'ar', 'value': 'سبستيان بنييرا'}, 'ay': {'language': 'ay', 'value': 'Sebastián Piñera'}, 'az': {'language': 'az', 'value': 'Sebastyan Pinyera'}, 'be': {'language': 'be', 'value': 'Себасцьян Піньера'}, 'bg': {'language': 'bg', 'value': 'Себастиан Пинера'}, 'br': {'language': 'br', 'value': 'Sebastián Piñera'}, 'ca': {'language': 'ca', 'value': 'Sebastián Piñera'}, 'cs': {'language': 'cs', 'value': 'Sebastián Piñera'}, 'da': {'language': 'da', 'value': 'Sebastián Piñera'}, 'el': {'language': 'el', 'valu

KeyboardInterrupt: 

In [ ]:
def fetch_wikidata_properties(qid):
    """
    Data una stringa 'Q306', restituisce un dizionario
    con tutte le proprietà e relativi valori che Wikidata
    rende disponibili per l'elemento.
    """
    client = Client()  # Inizializza il client
    entity = client.get(qid, load=True)  # Carica i dati dell'entità

    # 'entity.attributes' contiene i dati grezzi in formato JSON-like.
    # Esempio: 'claims' al suo interno ha P#, P#, ecc.
    data = entity.attributes  # è un dict

    return data

# Esempio di utilizzo
url = "http://www.wikidata.org/entity/Q321103"
qid = url.split('/')[-1]  # "Q306"

print(fetch_wikidata_properties(qid))

{'pageid': 308428, 'ns': 0, 'title': 'Q321103', 'lastrevid': 2182280166, 'modified': '2024-06-17T16:22:21Z', 'type': 'item', 'id': 'Q321103', 'labels': {'de': {'language': 'de', 'value': 'Bühl'}, 'cs': {'language': 'cs', 'value': 'Bühl'}, 'en': {'language': 'en', 'value': 'Bühl'}, 'nl': {'language': 'nl', 'value': 'Bühl'}, 'af': {'language': 'af', 'value': 'Bühl'}, 'an': {'language': 'an', 'value': 'Bühl'}, 'ast': {'language': 'ast', 'value': 'Bühl'}, 'bar': {'language': 'bar', 'value': 'Bühl'}, 'br': {'language': 'br', 'value': 'Bühl'}, 'ca': {'language': 'ca', 'value': 'Bühl'}, 'co': {'language': 'co', 'value': 'Bühl'}, 'cy': {'language': 'cy', 'value': 'Bühl'}, 'da': {'language': 'da', 'value': 'Bühl'}, 'de-at': {'language': 'de-at', 'value': 'Bühl'}, 'de-ch': {'language': 'de-ch', 'value': 'Bühl'}, 'en-ca': {'language': 'en-ca', 'value': 'Bühl'}, 'en-gb': {'language': 'en-gb', 'value': 'Bühl'}, 'eo': {'language': 'eo', 'value': 'Bühl'}, 'es': {'language': 'es', 'value': 'Bühl'}, 'e